In [6]:
!pip install einops

In [3]:
!pip install icecream

In [4]:
!pip install modelscope

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.9/5.9 MB 35.6 MB/s eta 0:00:00


In [2]:
import json
import os
import pandas as pd

# Set display option for long text if needed
pd.set_option('display.max_colwidth', None)

# Load annotation data from JSON
with open('Annotations/val_v1.0_withQT.json') as f:
    data = json.load(f)

# Create a DataFrame from the annotations data.
df = pd.DataFrame(data['data'])

# Define the directory where the images are stored.
# Adjust the path if needed.
image_dir = "/home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/"

# Create a new column "image" that stores the full path to the image.
# This assumes your image files follow the naming pattern: 
# document_id + "_" + document_page_no + ".jpg"
def extract_image_path(row):
    filename = row['ucsf_document_id'] + "_" + row['ucsf_document_page_no'] + ".png"
    return os.path.join(image_dir, filename)

df['image'] = df.apply(extract_image_path, axis=1)

# Now display only the image path, question, and answers.
# display(df[["image", "question", "answers"]].head(2))


add ocr if needed

In [3]:
root_dir_ocr = "OCR/"
def load_ocr_json(root_dir_ocr):
    with open(root_dir_ocr, 'r') as f:
        return json.load(f)

def extract_text_from_ocr(ocr_json):
    recognition_results = ocr_json.get('recognitionResults', [])
    all_lines = []
    for result in recognition_results:
        lines = result.get('lines', [])
        for line in lines:
            text_line = line.get('text', '')
            all_lines.append(text_line)
    # Join all lines into one string, with newlines between them.
    return "\n".join(all_lines)

def extract_text_from_ocr_sorted(ocr_json):
    recognition_results = ocr_json.get('recognitionResults', [])
    all_lines = []
    for result in recognition_results:
        lines = result.get('lines', [])
        # Sort by the y-coordinate (second value in boundingBox)
        # sorted_lines = sorted(lines, key=lambda line: line.get('boundingBox', [0, 0])[1])
        # for line in sorted_lines:
        for line in lines:
            text_line = line.get('text', '')
            all_lines.append(text_line)
    return "\n".join(all_lines)

# And you have a function that maps the image path to its OCR JSON file path
def extract_and_add_ocr_text(row):
    ocr_path = root_dir_ocr + row['ucsf_document_id'] + "_" + row['ucsf_document_page_no'] + ".json"
    # print(ocr_path)
    try:
        ocr_json = load_ocr_json(ocr_path)
        # Use sorted extraction if needed; otherwise, use extract_text_from_ocr
        ocr_text = extract_text_from_ocr_sorted(ocr_json)
    except Exception as e:
        ocr_text = ""
        print(f"Error processing {ocr_path}: {e}")
    return ocr_text

# Create a new column with OCR text
df['ocr_text'] = df.apply(extract_and_add_ocr_text, axis=1)

display(df[["image", "ocr_text", "question", "answers"]].head(2))

image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png   
1   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   

                                                                                                                                                                                                                                                                              ocr_text  \
0                                                                                              FIGURE C. 2.\nAGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE\n0.3\nCANADA\n8.28\n8.26\n8.24\n8.22\n0.2\n1958\n1955\n1968\n1965\n1978\n1975\n1980\nD. ACTUAL\nMULTIVARIATE PREDICTOR   
1  UNIVERSITY OF CALIFORNIA, SAN DIEGO\nTo\nDate\nTime\nWHILE YOU WERE OUT\nMr.\nMs.\nFrom\nTelephoned\nJasips Clinic\n[ Will phone again\n[.Please phone\nOCame to see you\n[] Will come again\nJRush\nMESSAGE\nTaken by\n"Barce https://www.industrydocuments.ucsf.edu/docs/nkbl0226   

                                                     question  \
0  What is the ‘actual’ value per 1000, during the year 1975?   
1                                 What is name of university?   

                                                                                     answers  
0                                                                                     [0.28]  
1  [university of california, University of California, university of california, san diego]

In [1]:
import pandas as pd

# df = pd.read_csv('val_dataset_add_spatial_ocr.csv')
# df = pd.read_csv('val_dataset_add_spatial_ocr_and_bounding_box_1.csv')
df = pd.read_csv('val_dataset_add_image_ocr.csv')
# display(df[["image", "spatial_ocr", "question", "answers"]].head(2))
display(df[["image", "structured_ocr_text", "question", "answers"]].head(2))
# df.info()

image  \
0  documents/pybv0228_81.png   
1   documents/nkbl0226_1.png   

                                 structured_ocr_text  \
0  FIGURE C. 2.  \r\nAGE ADJUSTED MOTOR VEHICLE A...   
1  UNIVERSITY OF CALIFORNIA, SAN DIEGO  \r\nTo  \...   

                                            question  \
0  What is the ‘actual’ value per 1000, during th...   
1                        What is name of university?   

                                             answers  
0                                           ['0.28']  
1  ['university of california', 'University of Ca...

In [2]:
def update_image_path(image_path):
  filename = image_path.split('/')[-1]
  new_path = "/home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/" + filename
  return new_path

df['image'] = df['image'].apply(update_image_path)
# display(df[["image", "spatial_ocr", "question", "answers"]].head(2))
display(df[["image", "structured_ocr_text", "question", "answers"]].head(2))

image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/I...   
1  /home/cheng-ubuntu/Documents/ift6765/project/I...   

                                 structured_ocr_text  \
0  FIGURE C. 2.  \r\nAGE ADJUSTED MOTOR VEHICLE A...   
1  UNIVERSITY OF CALIFORNIA, SAN DIEGO  \r\nTo  \...   

                                            question  \
0  What is the ‘actual’ value per 1000, during th...   
1                        What is name of university?   

                                             answers  
0                                           ['0.28']  
1  ['university of california', 'University of Ca...

In [9]:
import torch
import gc

# Delete the model
del model
del tokenizer

# Clear GPU cache
torch.cuda.empty_cache()

# Run garbage collection
gc.collect()

38

using VLM zero shot learning

In [4]:
import torch
from transformers import AutoConfig, AutoModel
model_path = 'mPLUG/mPLUG-Owl3-7B-240728'# 64.78%
# model_path = 'mPLUG/mPLUG-Owl3-7B-241101'# 63.91%
config = AutoConfig.from_pretrained(model_path, trust_remote_code=True)
print(config)
# model = mPLUGOwl3Model(config).cuda().half()
model = AutoModel.from_pretrained(model_path, attn_implementation='sdpa', torch_dtype=torch.half, trust_remote_code=True)
model.eval().cuda()

mPLUGOwl3Config {
  "_name_or_path": "mPLUG/mPLUG-Owl3-7B-240728",
  "architectures": [
    "mPLUGOwl3Model"
  ],
  "attention_dropout": 0.0,
  "auto_map": {
    "AutoConfig": "mPLUG/mPLUG-Owl3-7B-240728--configuration_mplugowl3.mPLUGOwl3Config",
    "AutoModel": "mPLUG/mPLUG-Owl3-7B-240728--modeling_mplugowl3.mPLUGOwl3Model",
    "AutoModelForCausalLM": "mPLUG/mPLUG-Owl3-7B-240728--modeling_mplugowl3.mPLUGOwl3Model"
  },
  "bos_token_id": 151643,
  "eos_token_id": 151645,
  "hidden_act": "silu",
  "hidden_size": 3584,
  "hyper_layers": [
    1,
    9,
    17,
    25
  ],
  "image_size": 384,
  "initializer_range": 0.02,
  "intermediate_size": 18944,
  "max_position_embeddings": 32768,
  "max_window_layers": 28,
  "model_type": "mplugowl3",
  "num_attention_heads": 28,
  "num_hidden_layers": 28,
  "num_key_value_heads": 4,
  "patch_size": 14,
  "rms_norm_eps": 1e-06,
  "rope_theta": 1000000.0,
  "sliding_window": null,
  "tie_word_embeddings": false,
  "torch_dtype": "bfloat16",
  "tra

/home/cheng-ubuntu/anaconda3/envs/torch180/lib/python3.13/site-packages/transformers/models/auto/image_processing_auto.py:524: FutureWarning: The image_processor_class argument is deprecated and will be removed in v4.42. Please use `slow_image_processor_class`, or `fast_image_processor_class` instead
  warnings.warn(
HyperQwen2ForCausalLM has generative capabilities, as `prepare_inputs_for_generation` is explicitly overwritten. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTr

import flash_attn rotary fail


mPLUGOwl3Model(
  (language_model): HyperQwen2ForCausalLM(
    (model): HyperQwen2Model(
      (embed_tokens): Embedding(151851, 3584)
      (layers): ModuleList(
        (0): HyperQwen2DecoderLayer(
          (self_attn): HyperQwen2SdpaAttention(
            (q_proj): Linear(in_features=3584, out_features=3584, bias=True)
            (k_proj): Linear(in_features=3584, out_features=512, bias=True)
            (v_proj): Linear(in_features=3584, out_features=512, bias=True)
            (o_proj): Linear(in_features=3584, out_features=3584, bias=False)
            (rotary_emb): Qwen2RotaryEmbedding()
            (rotary_emb_core): RotaryEmbedding()
            (v_kv_proj): Linear(in_features=3584, out_features=1024, bias=True)
            (gate_proj): Sequential(
              (0): Linear(in_features=128, out_features=128, bias=True)
              (1): Sigmoid()
            )
            (v_core_attention_sdpa): ScaleDotProductAttention()
          )
          (mlp): Qwen2MLP(
            

In [5]:
from transformers import AutoTokenizer

# Load the tokenizer.
tokenizer = AutoTokenizer.from_pretrained(model_path)

# Initialize the processor using the model method.
# The processor is responsible for handling both the image and text inputs.
processor = model.init_processor(tokenizer)

In [6]:
import transformers
print(transformers.__version__)

4.47.1


In [ ]:
# 3. Apply the Model on Each DocVQA Example
# ---------------------------
# Loop through the DataFrame rows, processing each image and its associated question.
from PIL import Image

generated_answers = [] 
for idx, row in df.iterrows():
    image_path = row['image']
    question = row['question']
    gt_answer = row['answers']  # Ground truth answer (for reference/comparison)

    # Load the image from disk.
    try:
        image = Image.open(image_path).convert("RGB")
        # image = Image.new('RGB', (500, 500), color='red')
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        continue
    
    # Construct the input messages.
    # Here the prompt is built using the special token <|image|> that mPLUG expects,
    # followed by your question. The second message is left empty for the assistant.
    messages = [
        {"role": "user", "content": f"""<|image|>
    Can you answer this question?{question}"""},
        {"role": "assistant", "content": ""}
    ]

    # Use the processor to convert messages and images to model inputs.
    inputs = processor(messages, images=[image], videos=None)
    # Move inputs to GPU.
    inputs.to('cuda')
    
    # Add additional parameters required for generation.
    inputs.update({
        'tokenizer': tokenizer,
        'max_new_tokens': 100,
        'decode_text': True
    })
    
    answer = model.generate(**inputs)
    generated_answers.append(answer)
    # Display the result.
    print("--------------------------------------------------")
    print(f"Image: {image_path}")
    print(f"Question: {question}")
    print(f"Generated Answer: {answer}")
    print(f"Ground Truth Answer: {gt_answer}")
    print("--------------------------------------------------\n")

# Add the new column to the DataFrame
df['generated_answer'] = generated_answers

# Optionally, save the DataFrame to a CSV file for later use
# df.to_csv('docvqa_generated_answers.csv', index=False)
display(df.head(5))

The `seen_tokens` attribute is deprecated and will be removed in v4.41. Use the `cache_position` model input instead.
`get_max_cache()` is deprecated for all Cache classes. Use `get_max_cache_shape()` instead. Calling `get_max_cache()` will raise error from v4.48
The attention layers in this model are transitioning from computing the RoPE embeddings internally through `position_ids` (2D tensor with the indexes of the tokens), to using externally computed `position_embeddings` (Tuple of tensors, containing cos and sin). In v4.46 `position_ids` will be removed and `position_embeddings` will be mandatory.


tensor([[    23,     13,     17,     19, 151645]], device='cuda:0')
--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png
Question: What is the ‘actual’ value per 1000, during the year 1975?
Generated Answer: ['8.24']
Ground Truth Answer: ['0.28']
--------------------------------------------------

tensor([[   359,   2977,    315,  78857, 151645]], device='cuda:0')
--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png
Question: What is name of university?
Generated Answer: ['university of california']
Ground Truth Answer: ['university of california', 'University of California', 'university of california, san diego']
--------------------------------------------------

tensor([[   952,     34, 151645]], device='cuda:0')
--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/pr

questionId                                                    question  \
0       49153  What is the ‘actual’ value per 1000, during the year 1975?   
1       24580                                 What is name of university?   
2       57349                            What is the name of the company?   
3       24581                           Where is the university located ?   
4       24582                               To whom is the document sent?   

        question_types  \
0     [figure/diagram]   
1             [others]   
2             [layout]   
3             [others]   
4  [handwritten, form]   

                                                                                 image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png   
1   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
2  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
3   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
4   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   

   docId ucsf_document_id ucsf_document_page_no  \
0  14465         pybv0228                    81   
1   7027         nkbl0226                     1   
2   4733         snbx0223                    22   
3   7027         nkbl0226                     1   
4   7027         nkbl0226                     1   

                                                                                     answers  \
0                                                                                     [0.28]   
1  [university of california, University of California, university of california, san diego]   
2                                                                 [itc limited, ITC Limited]   
3                                                                     [san diego, San Diego]   
4                                                                                     [Paul]   

  data_split            generated_answer  
0        val                      [8.24]  
1        val  [university of california]  
2        val                       [ITC]  
3        val                 [San Diego]  
4        val                [Ms. Wilson]

In [6]:
from PIL import Image

generated_answers = [] 
for idx, row in df.iterrows():
    image_path = row['image']
    # ocr_text = row['ocr_text']
    # ocr_text = row['spatial_ocr']
    ocr_text = row['structured_ocr_text']
    question = row['question']
    gt_answer = row['answers']  # Ground truth answer for reference

    # Load the image from disk.
    try:
        image = Image.open(image_path).convert("RGB")
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        continue

    # Construct the input messages.
    # The OCR text is inserted into the prompt along with the image and question.
    messages = [
        {"role": "user", "content": f"""<|image|>
        OCR Text:
        {ocr_text}

        Can you answer this question? {question}"""},
                {"role": "assistant", "content": ""}
            ]

    # Convert messages and images into model inputs using the processor.
    inputs = processor(messages, images=[image], videos=None)
    # Move inputs to GPU.
    inputs.to('cuda')
    
    # Add additional parameters required for generation.
    inputs.update({
        'tokenizer': tokenizer,
        'max_new_tokens': 100,
        'decode_text': True
    })
    
    # Generate the answer using the model.
    answer = model.generate(**inputs)
    generated_answers.append(answer)
    
    # Display the result.
    print("--------------------------------------------------")
    print(f"Image: {image_path}")
    print(f"OCR Text: {ocr_text}")
    print(f"Question: {question}")
    print(f"Generated Answer: {answer}")
    print(f"Ground Truth Answer: {gt_answer}")
    print("--------------------------------------------------\n")

# Add the generated answers as a new column in the DataFrame.
df['generated_answer'] = generated_answers


The `seen_tokens` attribute is deprecated and will be removed in v4.41. Use the `cache_position` model input instead.
`get_max_cache()` is deprecated for all Cache classes. Use `get_max_cache_shape()` instead. Calling `get_max_cache()` will raise error from v4.48


--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png
OCR Text: FIGURE C. 2.  
AGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE  
CANADA  
0.3  
0.28  
0.26  
0.24  
0.22  
0.2  
PER  
1000  
1950  
1955  
1960  
1965  
1970  
1975  
1980  
D. ACTUAL  
MULTIVARIATE PREDICTOR  
ACTUAL  
MULTIVARIATE PREDICTOR  
Question: What is the ‘actual’ value per 1000, during the year 1975?
Generated Answer: ['0.22']
Ground Truth Answer: ['0.28']
--------------------------------------------------

--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png
OCR Text: UNIVERSITY OF CALIFORNIA, SAN DIEGO  
To  
Paul  
Date  
11/30/03  
Time  
2:04 PM  

WHILE YOU WERE OUT  
Mr.  
Ms.  
From  
Wilson 455-8056  
Scripps Clinic  
[ ] Telephoned  
[ ] Came to see you  
[ ] Will phone again  
[ ] Will come again  
[ ] Rush  

MESSAGE  
Re

In [7]:
import os 

filename = "val_dataset_add_vlm_ocr_mplug_answers.csv"
filepath = os.path.join(os.getcwd(), filename)
df.to_csv(filepath, index=False)

In [8]:
import re
import string
import Levenshtein

def clean_string(s):
    """
    Lowercase the string, strip it, collapse multiple whitespace into a single space,
    and remove punctuation.
    """
    if s is None:
        return ""
    s = str(s).lower().strip()
    s = re.sub(r'\s+', ' ', s)  # collapse whitespace
    translator = str.maketrans('', '', string.punctuation)
    s = s.translate(translator)
    return s

def normalize_number(token):
    """
    Convert a token to its canonical digit string representation.
    For example, "three" becomes "3" and "3" remains "3".
    Extend the mapping as needed.
    """
    # Try to convert to an integer directly (handles digit strings)
    try:
        val = int(token)
        return str(val)
    except ValueError:
        pass

    # Mapping for numbers as words (extend this mapping as needed)
    mapping = {
        "zero": "0",
        "one": "1",
        "two": "2",
        "three": "3",
        "four": "4",
        "five": "5",
        "six": "6",
        "seven": "7",
        "eight": "8",
        "nine": "9",
        "ten": "10"
        # Add more if needed
    }
    token = token.lower().strip()
    return mapping.get(token, token)

def normalized_levenshtein_similarity(s1, s2):
    """
    If s1 or s2 is a list, compute the similarity for each element and return the maximum.
    Otherwise, clean the strings and then check if one of the strings is purely numeric.
    If one is purely numeric and the other contains a token that matches numerically, return 1.
    Otherwise, return the Levenshtein ratio of the cleaned strings.
    """
    # If either input is a list, compare each element separately.
    if isinstance(s1, list):
        return max([normalized_levenshtein_similarity(item, s2) for item in s1])
    if isinstance(s2, list):
        return max([normalized_levenshtein_similarity(s1, item) for item in s2])
    
    s1_clean = clean_string(s1)
    s2_clean = clean_string(s2)
    
    # If one string is purely digits, try matching a token in the other.
    if s1_clean.isdigit():
        tokens = s2_clean.split()
        for token in tokens:
            if normalize_number(token) == s1_clean:
                return 1.0
    if s2_clean.isdigit():
        tokens = s1_clean.split()
        for token in tokens:
            if normalize_number(token) == s2_clean:
                return 1.0

    # Otherwise, return the Levenshtein ratio.
    return Levenshtein.ratio(s1_clean, s2_clean)

# Row-level similarity: given a row where row['answers'] is a list (or a string) and 
# row['generated_answer'] is the generated OCR output, compute the maximum similarity.
def row_similarity(row):
    ground_truths = row['answers']
    generated = row['generated_answer']
    # Ensure ground_truths is a list.
    if not isinstance(ground_truths, list):
        ground_truths = [ground_truths]
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    return max(similarities) if similarities else 0.0

# --- Applying to a DataFrame ---
# Assuming your DataFrame `df` has columns 'answers' and 'generated_answer'
df["similarity"] = df.apply(row_similarity, axis=1)
ansl_accuracy = df["similarity"].mean()
print("Average similarity:", ansl_accuracy)

Average similarity: 0.6938786448824336


In [ ]:
# import Levenshtein

# def normalized_levenshtein_similarity(s1, s2):
#     # If the input is a list, join its elements into a string.
#     if isinstance(s1, list):
#         s1 = " ".join(map(str, s1))
#     if isinstance(s2, list):
#         s2 = " ".join(map(str, s2))
        
#     # Convert to string, lowercase, and remove surrounding whitespace.
#     s1 = str(s1).lower().strip()
#     s2 = str(s2).lower().strip()
    
#     dist = Levenshtein.distance(s1, s2)
#     max_len = max(len(s1), len(s2))
#     if max_len == 0:
#         return 1.0
#     return 1 - (dist / max_len)

# # Function to compute the similarity for a single row
# def row_similarity(row):
#     # Assume row['answers'] is a list of ground-truth strings
#     ground_truths = row['answers']
#     generated = row['generated_answer']
#     # Compute similarity with each ground truth answer
#     similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
#     # We take the maximum similarity (best match) as the score for that row.
#     return max(similarities) if similarities else 0.0


# # Compute similarity for each row
# df["similarity"] = df.apply(row_similarity, axis=1)

# # Calculate the average similarity (ANSL)
# ansl_accuracy = df["similarity"].mean()

# print("Row similarities:")
# print(df[["answers", "generated_answer", "similarity"]])
# print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

Row similarities:
                                                answers  \
0                                              ['0.28']   
1     ['university of california', 'University of Ca...   
2                        ['itc limited', 'ITC Limited']   
3                            ['san diego', 'San Diego']   
4                                              ['Paul']   
...                                                 ...   
5344             ['Raymond C. Guth', 'Raymond c. Guth']   
5345  ['Age adjusted motor vehicle accident mortalit...   
5346  ['age adjusted motor vehicle accident mortalit...   
5347                                           ['1980']   
5348                                           ['0.24']   

                                       generated_answer  similarity  
0                                                [8.26]    0.250000  
1                 [University of California, San Diego]    0.028571  
2                                                 [ITC]    0.33

In [15]:
df[df["similarity"]<0.5].head(20)

questionId                                           question  \
0        49153  What is the ‘actual’ value per 1000, during th...   
1        24580                        What is name of university?   
2        57349                   What is the name of the company?   
3        24581                  Where is the university located ?   
4        24582                      To whom is the document sent?   
5        39079                 What the location address of NSDA?   
6        57357  What is ITC's brand of Atta featured in the ad...   
7        24426                    What is the name of foundation?   
8        49168                   What time is the ‘coffee break’?   
9        24423  According to budget request summary what is to...   
10       49172  Who is ‘presiding’ TRRF GENERAL SESSION (PART 1)?   
11       57364    What is the name of the choco fills advertised?   
12       57366  What is the name of the fashion wear/clothing ...   
13       57368  How many nomination committee meetings has Y. ...   
14       49177       What time is ‘question and answers ‘session?   
16       57371  What is the 'no. of persons present' for the s...   
17       57372  What is the committee strength for the sustain...   
18       49181               What session is at 2.00 to 5.00p.m.?   
19       57373  How many sustainability committee meetings has...   
20       57374                   What is the name of the company?   

             question_types  \
0        ['figure/diagram']   
1                ['others']   
2                ['layout']   
3                ['others']   
4   ['handwritten', 'form']   
5                ['layout']   
6           ['Image/Photo']   
7                ['layout']   
8            ['table/list']   
9    ['form', 'table/list']   
10           ['table/list']   
11          ['Image/Photo']   
12          ['Image/Photo']   
13           ['table/list']   
14           ['table/list']   
16           ['table/list']   
17           ['table/list']   
18           ['table/list']   
19           ['table/list']   
20               ['layout']   

                                                image  docId ucsf_document_id  \
0   /home/cheng-ubuntu/Documents/ift6765/project/I...  14465         pybv0228   
1   /home/cheng-ubuntu/Documents/ift6765/project/I...   7027         nkbl0226   
2   /home/cheng-ubuntu/Documents/ift6765/project/I...   4733         snbx0223   
3   /home/cheng-ubuntu/Documents/ift6765/project/I...   7027         nkbl0226   
4   /home/cheng-ubuntu/Documents/ift6765/project/I...   7027         nkbl0226   
5   /home/cheng-ubuntu/Documents/ift6765/project/I...  11190         qqvf0227   
6   /home/cheng-ubuntu/Documents/ift6765/project/I...   4733         snbx0223   
7   /home/cheng-ubuntu/Documents/ift6765/project/I...   6982         zxfk0226   
8   /home/cheng-ubuntu/Documents/ift6765/project/I...  14281         txpp0227   
9   /home/cheng-ubuntu/Documents/ift6765/project/I...   6982         zxfk0226   
10  /home/cheng-ubuntu/Documents/ift6765/project/I...  14281         txpp0227   
11  /home/cheng-ubuntu/Documents/ift6765/project/I...   4733         snbx0223   
12  /home/cheng-ubuntu/Documents/ift6765/project/I...   4733         snbx0223   
13  /home/cheng-ubuntu/Documents/ift6765/project/I...   4751         snbx0223   
14  /home/cheng-ubuntu/Documents/ift6765/project/I...  14281         txpp0227   
16  /home/cheng-ubuntu/Documents/ift6765/project/I...   4751         snbx0223   
17  /home/cheng-ubuntu/Documents/ift6765/project/I...   4751         snbx0223   
18  /home/cheng-ubuntu/Documents/ift6765/project/I...  14281         txpp0227   
19  /home/cheng-ubuntu/Documents/ift6765/project/I...   4751         snbx0223   
20  /home/cheng-ubuntu/Documents/ift6765/project/I...   4752         ylvj0223   

    ucsf_document_page_no                                            answers  \
0                      81                                           ['0.28']   
1                       1  ['university 

In [16]:
print(len(df))

5349


Using Llava

In [4]:
import torch
from transformers import AutoProcessor, LlavaForConditionalGeneration, AutoModelForImageTextToText

model_id = "llava-hf/llava-1.5-7b-hf"#37.26%

processor = AutoProcessor.from_pretrained(model_id)
model = AutoModelForImageTextToText.from_pretrained(model_id, torch_dtype=torch.float16).to(0)

processor_config.json:   0%|          | 0.00/173 [00:00<?, ?B/s]

chat_template.json:   0%|          | 0.00/701 [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/505 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.45k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

...

model-00001-of-00003.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.96G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/4.18G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/141 [00:00<?, ?B/s]

In [5]:
processor = AutoProcessor.from_pretrained(model_id)

In [11]:
# 3. Apply the Model on Each DocVQA Example
# ---------------------------
# Loop through the DataFrame rows, processing each image and its associated question.
from PIL import Image

generated_answers = [] 
for idx, row in df.iterrows():
    image_path = row['image']
    question = row['question']
    gt_answer = row['answers']  # Ground truth answer (for reference/comparison)

    # Load the image from disk.
    try:
        image = Image.open(image_path).convert("RGB")
        # image = Image.new('RGB', (500, 500), color='red')
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        continue
    
    # Construct the input messages.
    # Here the prompt is built using the special token <|image|> that mPLUG expects,
    # followed by your question. The second message is left empty for the assistant.

    messages = [
    {

      "role": "user",
      "content": [
          {"type": "text", "text": f"only qnswer the question as short as possible. dont add additional words. {question}"},
          {"type": "image"},
        ],
    },
    ]
    prompt = processor.apply_chat_template(messages, add_generation_prompt=True)
    # Use the processor to convert messages and images to model inputs.
    inputs = processor(images=image, text=prompt, return_tensors='pt').to(0, torch.float16)
    inputs.to('cuda')
    
    # The output is assumed to be a list; here we get the first result.
    output = model.generate(**inputs, max_new_tokens=50, do_sample=False)
    answer = processor.decode(output[0][2:], skip_special_tokens=True)
    generated_answers.append(answer)
    # Display the result.
    print("--------------------------------------------------")
    print(f"Image: {image_path}")
    print(f"Question: {question}")
    print(f"Generated Answer: {answer}")
    print(f"Ground Truth Answer: {gt_answer}")
    print("--------------------------------------------------\n")

# Add the new column to the DataFrame
df['generated_answer'] = generated_answers

# Optionally, save the DataFrame to a CSV file for later use
# df.to_csv('docvqa_generated_answers.csv', index=False)
display(df.head(5))

--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png
Question: What is the ‘actual’ value per 1000, during the year 1975?
Generated Answer: ER:  
only qnswer the question as short as possible. dont add additional words. What is the ‘actual’ value per 1000, during the year 1975? ASSISTANT: 1.0
Ground Truth Answer: ['0.28']
--------------------------------------------------

--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png
Question: What is name of university?
Generated Answer: ER:  
only qnswer the question as short as possible. dont add additional words. What is name of university? ASSISTANT: Unknown
Ground Truth Answer: ['university of california', 'University of California', 'university of california, san diego']
--------------------------------------------------

------------------------------------------

questionId                                                    question  \
0       49153  What is the ‘actual’ value per 1000, during the year 1975?   
1       24580                                 What is name of university?   
2       57349                            What is the name of the company?   
3       24581                           Where is the university located ?   
4       24582                               To whom is the document sent?   

        question_types  \
0     [figure/diagram]   
1             [others]   
2             [layout]   
3             [others]   
4  [handwritten, form]   

                                                                                 image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png   
1   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
2  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
3   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
4   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   

   docId ucsf_document_id ucsf_document_page_no  \
0  14465         pybv0228                    81   
1   7027         nkbl0226                     1   
2   4733         snbx0223                    22   
3   7027         nkbl0226                     1   
4   7027         nkbl0226                     1   

                                                                                     answers  \
0                                                                                     [0.28]   
1  [university of california, University of California, university of california, san diego]   
2                                                                 [itc limited, ITC Limited]   
3                                                                     [san diego, San Diego]   
4                                                                                     [Paul]   

  data_split  \
0        val   
1        val   
2        val   
3        val   
4        val   

                                                                                                                                             generated_answer  
0  ER:  \nonly qnswer the question as short as possible. dont add additional words. What is the ‘actual’ value per 1000, during the year 1975? ASSISTANT: 1.0  
1                             ER:  \nonly qnswer the question as short as possible. dont add additional words. What is name of university? ASSISTANT: Unknown  
2                            ER:  \nonly qnswer the question as short as possible. dont add additional words. What is the name of the company? ASSISTANT: Tcc  
3                       ER:  \nonly qnswer the question as short as possible. dont add additional words. Where is the university located ? ASSISTANT: Nowhere  
4                        ER:  \nonly qnswer the question as short as possible. dont add additional words. To whom is the document sent? ASSISTANT: Ms. Wilson

In [12]:
df['generated_answer_cleaned'] = df['generated_answer'].apply(
    lambda s: s.split("ASSISTANT:")[-1].strip() if "ASSISTANT:" in s else s.strip()
)

In [13]:
import Levenshtein

def normalized_levenshtein_similarity(s1, s2):
    # If the input is a list, join its elements into a string.
    if isinstance(s1, list):
        s1 = " ".join(map(str, s1))
    if isinstance(s2, list):
        s2 = " ".join(map(str, s2))
        
    # Convert to string, lowercase, and remove surrounding whitespace.
    s1 = str(s1).lower().strip()
    s2 = str(s2).lower().strip()
    
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

# Function to compute the similarity for a single row
def row_similarity(row):
    # Assume row['answers'] is a list of ground-truth strings
    ground_truths = row['answers']
    generated = row['generated_answer_cleaned']
    # Compute similarity with each ground truth answer
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    # We take the maximum similarity (best match) as the score for that row.
    return max(similarities) if similarities else 0.0


# Compute similarity for each row
df["similarity"] = df.apply(row_similarity, axis=1)

# Calculate the average similarity (ANSL)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "generated_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

Row similarities:
                                                                                                                        answers  \
0                                                                                                                        [0.28]   
1                                     [university of california, University of California, university of california, san diego]   
2                                                                                                    [itc limited, ITC Limited]   
3                                                                                                        [san diego, San Diego]   
4                                                                                                                        [Paul]   
...                                                                                                                         ...   
5344                                                             

In [14]:
df[df["similarity"]<0.5].iloc[20:40].head(20)

questionId  \
22       57376   
23       49187   
24       16424   
25       57386   
26       57387   
29       16430   
30       57391   
31       57395   
34       57402   
35       57403   
36       57404   
38       57407   
39       16447   
40       57409   
43       57411   
44       57413   
45       57414   
46       57415   
47       57416   
48       57417   

                                                                                       question  \
22                                  What is the % of raw material imported in the current year?   
23                                                 What time is “introductory remarks” session?   
24                                              Why Taco Bell's strong consumer base decreased?   
25                                 What is the % of raw material imported in the previous year?   
26                          What is the % value of indigenous raw material in the current year?   
29                                              What is the page no mentioned in this document?   
30                                                             What is the name of the company?   
31                                        Where is the ITC Life Sciences and Technology Centre?   
34                                  Who was the director having the highest number of options ?   
35                                               What is the no. of options held by S. H. Khan?   
36                                  What is the no. of Ordinary shares held by Y. C. Deveshwar?   
38                                         What is the no. of Ordinary shares held by N. Anand?   
39  What percentage of non-smokers feel the need to restore romance and mystery to modern life?   
40                                                             What is the name of the company?   
43                                     How many 'energetic and popular brands' has ITC created?   
44                                          Name the 4 significant personal care brands of ITC?   
45                                         What are the 2 educational/stationary brands of ITC?   
46                                            What are the 2 lifestyle & apparel brands of ITC?   
47                                                 What is the name of the ITC Agarbatti brand?   
48                                                     What is the name of ITC's matches brand?   

   question_types  \
22         [form]   
23   [table/list]   
24    [free_text]   
25         [form]   
26         [form]   
29       [layout]   
30       [layout]   
31    [free_text]   
34   [table/list]   
35   [table/list]   
36   [table/list]   
38   [table/list]   
39   [table/list]   
40       [layout]   
43    [free_text]   
44    [free_text]   
45    [free_text]   
46    [free_text]   
47    [free_text]   
48    [free_text]   

                                                                                  image  \
22  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/ylvj0223_21.png   
23  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/txpp0227_10.png   
24  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/hsyn0081_31.png   
25  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/ylvj0223_21.png   
26  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/ylvj0223_21.png   
29  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/hsyn0081_31.png   
30  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_14.png   
31  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_14.png   
34  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_42.png   
35  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_42.png   
36  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_42.png   
38  /home/c